In [1]:
import findspark
findspark.init()
import pyspark

conf = pyspark.SparkConf()
conf.set("spark.driver.bindAddress", "127.0.0.1")  # Localhost
conf = conf.setMaster("local[*]")
conf = conf.setAppName("App")

sc = pyspark.SparkContext(conf=conf)




Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
24/11/28 23:31:50 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [2]:
# Einlesen der Flugdaten von einem Tag + entfernen des ersten Datensatzes (Header)
myFileRDD = sc.textFile('/Users/I750252/Downloads/20230126_merged.csv')
header = myFileRDD.first()

dataRDD = myFileRDD.filter(lambda line: line != header)
#print(dataRDD.take(5))

# Allgemeine Datenanalyse
# Anzahl an Datensätzen
amount_of_data = dataRDD.count()
print(f"Die Anzahl an Datensätzen (Flugtracker) beträgt {amount_of_data}")

#Erfassen des Zeitraums in dem Daten erhoben wurden
start_time = dataRDD.map(lambda line: line.split(',')[1]).min()
end_time = dataRDD.map(lambda line: line.split(',')[1]).max()
time_zone = start_time[-4:-1]

print(f"Die Daten erfassten Bewegungen von Flug- und Bodenobjekten im Zeitraum vom {start_time.replace('"', '').replace('+00', '')} bis zum {end_time.replace('"', '').replace('+00', '')} (Zeitzone: {time_zone})")

#Geographische Analyse des betrachteten Luftraums
# Längengrade (vermutlich Spalte mit Index 4 und 5)
min_longitude = dataRDD.map(lambda line: float(line.split(',')[4])).min()
max_longitude = dataRDD.map(lambda line: float(line.split(',')[4])).max()

# Breitengrade (vermutlich Spalte mit Index 5 und 6)
min_latitude = dataRDD.map(lambda line: float(line.split(',')[3])).min()
max_latitude = dataRDD.map(lambda line: float(line.split(',')[3])).max()

# Ausgabe mit Zeitinformationen und geografischen Koordinaten
print("")
print(f"Geografische Abdeckung:")
print(f"Längengrade: von {min_longitude:.4f}° bis {max_longitude:.4f}°")
print(f"Breitengrade: von {min_latitude:.4f}° bis {max_latitude:.4f}°")

Die Anzahl an Datensätzen (Flugtracker) beträgt 1389565
Die Daten erfassten Bewegungen von Flug- und Bodenobjekten im Zeitraum vom 2023/01/26 00:00:01 bis zum 2023/01/26 23:59:59 (Zeitzone: +00)

Geografische Abdeckung:
Längengrade: von -12.5352° bis 13.8460°
Breitengrade: von 36.0001° bis 54.1166°


In [3]:
import folium

# Zentrum des Bereichs berechnen
center_lat = (min_latitude + max_latitude) / 2
center_lon = (min_longitude + max_longitude) / 2

# Karte erstellen
m = folium.Map(location=[center_lat, center_lon], zoom_start=5)

# Rechteck auf der Karte hinzufügen
bounds = [[min_longitude, min_longitude], [max_latitude, min_latitude]]
folium.Rectangle(
    bounds=bounds,
    color="red",
    weight=2,
    fill=True,
    fill_color="blue",
    fill_opacity=0.2,
    popup="Geographischer Bereich"
).add_to(m)

# Karte anzeigen
m.save("geographic_area.html")
print(f"Die Daten wurden in folgendem Luftraum erhoben:")
m


Die Daten wurden in folgendem Luftraum erhoben:


In [ ]:
# Umstrukturierung der Daten zur Analyse der Flugzeuge
# Funktion zum Parsen einer Zeile
def parse_line(line):
    parts = line.split(',')
    return (
        parts[2].strip('"'),  # Key: Flugzeug-ID (icao24)
        {  # Value: Alle relevanten Daten als Dictionary
            "time": parts[1].strip('"'),
            "lat": float(parts[3].strip('"')),
            "lon": float(parts[4].strip('"')),
            "onground": int(parts[9].strip('"'))
        }
    )

# RDD transformieren: Gruppiere die Daten nach Flugzeug-ID
flights_rdd = dataRDD.map(parse_line).groupByKey().mapValues(list)

#Anzahl der Flugzeuge, die innerhalb einer Stunde im französischen Luftraum aktiv waren
amount_of_aircrafts = flights_rdd.count()
print(f"Anzahl der zum betrachteten Zeitpunkt aktiven Flug- und Bodenobjekte: {amount_of_aircrafts}")

#print(flights_rdd.take(2))


Anzahl der zum betrachteten Zeitpunkt aktiven Flug- und Bodenobjekte: 6938


In [ ]:
#Einlesen der Flugzeug-Typ Daten + entfernen des ersten Datensatzes (Header)
myTypeRDD = sc.textFile('/Users/I750252/Downloads/aircraft-type.csv')
myTypeRDD.take(8)
header = myTypeRDD.first()

typeRDD = myTypeRDD.filter(lambda line: line != header)
count_icao = typeRDD.distinct().count()

print(f"Anzahl der weltweit gemeldeten, eindeutigen Flug- und Bodenobjekte {count_icao}")

Anzahl der gemeldeten, eindeutigen Flug- und Bodenobjekte 601337


In [6]:
def parse_type(line):
    parts = line.split(',')
    # Baseline-Verarbeitung ohne unnötige Komplexität
    return (
        parts[0].strip("'"),  # Flugzeug-ID (icao24)
        {
            "description": parts[5].strip("'") if len(parts) > 4 else "",
            "manufacturer": parts[13].strip("'") if len(parts) > 12 else "",
            "model": parts[14].strip("'") if len(parts) > 14 else "",
            "type": parts[15].strip("'") if len(parts) > 15 else "",
            "airline": parts[18].strip("'") if len(parts) > 16 else ""
        }
    )

# RDD transformieren: Ausgewählte Daten beziehen
cleaned_type_rdd = typeRDD.map(parse_type)
#cleaned_type_rdd.take(5)


info = cleaned_type_rdd.filter(lambda x: x[0] == "3c48a3").collect()
print(info)



[('3c48a3', {'description': '', 'manufacturer': 'Boeing', 'model': 'Boeing 737 330', 'type': '0', 'airline': 'LUFTHANSA'})]


In [12]:
# Beschreibung für jeden Datensatz hinzufügen
result_rdd = flights_rdd.leftOuterJoin(cleaned_type_rdd)
result_rdd.take(1)
# Transformiere das Ergebnis, um die Daten zu kombinieren
# Behalte die Beschreibung zuerst, gefolgt von den Flugdaten
combined_rdd = result_rdd.map(lambda x: (
    x[0],  # Flugzeug-ID
    {
        "aircraft_info": x[1][1] if x[1][1] else {},  # Beschreibung, falls vorhanden
        "flight_data": x[1][0]  # Flugdaten
    }
))

# Ergebnisse anzeigen
#combined_rdd.take(10)

In [14]:
#Ermittlung der Anzahl an Flug-Datensätze pro Flugzeug
countdatasetsRDD = combined_rdd.map(lambda x: (x[0],len(x[1]['flight_data']))).sortBy(lambda x: x[1], ascending=False)
#print(countdatasetsRDD.take(10))


# Bestimmung Flugstatus
airRDD = combined_rdd.map(lambda x: (x[0], x[1]['flight_data'][-1]["onground"]))
onground = airRDD.filter(lambda x: x[1]==1).count()
inair = airRDD.filter(lambda x: x[1]==0).count()

print("Flugobjekte aktuell in der Luft: " + str(onground))
print("Flugobjekte aktuell am Boden: " + str(inair))


# Ermittlung wie viele nur in der Luft waren, wie viele nur am Boden und wie viele beides waren an einem Tag
nextRDD = combined_rdd.map(lambda x: (x[0], sum(datapoint["onground"] for datapoint in x[1]['flight_data']), len(x[1]['flight_data'])))
#print(nextRDD.take(1))
#Quotienten berechnen um zu schauen wer gelandet ist und wer nicht
calculatedRDD = nextRDD.map(lambda x: (x[0], x[1]/x[2]))
#print(calculatedRDD.take(1))

not_started = calculatedRDD.filter(lambda x: x[1] == 1).count()
print(f"Es sind so viele Objekte nicht am Boden geblieben: {not_started}")
not_landed = calculatedRDD.filter(lambda x: x[1] == 0).count()
print(f"Es sind so viele Objekte nicht gelandet: {not_landed}")
startet_or_landed = calculatedRDD.filter(lambda x: x[1] < 1 and x[1] >0).count()
print(f"Es sind so viele Objekte gestartet oder gelandet: {startet_or_landed}")


# Anzahl Starts und Anzahl Landungen

Flugobjekte aktuell in der Luft: 1779
Flugobjekte aktuell am Boden: 5159
Es sind so viele Objekte nicht am Boden geblieben: 603
Es sind so viele Objekte nicht gelandet: 2201
Es sind so viele Objekte gestartet oder gelandet: 4134


In [15]:
import folium
from IPython.display import display

# Die Flugzeug-ID, die visualisiert werden soll
selected_icao24 = "00cf06"

# Filtere die Daten für die spezifische Flugzeug-ID im RDD
filtered_data = combined_rdd.filter(lambda x: x[0] == selected_icao24).collect()

if filtered_data:
    # Hole die Daten für das ausgewählte Flugzeug
    icao24, route_data = filtered_data[0]
    aircraft_info = route_data["aircraft_info"]  # Zugriff auf die Flugzeugbeschreibung
    flight_data = route_data["flight_data"]  # Zugriff auf die Flugdaten

    print(f"Flugzeug-ID: {icao24}")
    print(f"Flugzeugtyp: {aircraft_info['type']}")  # Flugzeugtyp anzeigen

    # Erstelle die Karte, zentriert auf den ersten Datenpunkt
    first_lat = flight_data[0]["lat"]
    first_lon = flight_data[0]["lon"]
    mymap = folium.Map(location=[first_lat, first_lon], zoom_start=12)

    # Zeichne Linien zwischen aufeinanderfolgenden Punkten
    for i in range(len(flight_data) - 1):
        point_a = flight_data[i]
        point_b = flight_data[i + 1]

        # Zeichne nur Linien, wenn beide Punkte gültige Koordinaten haben
        if point_a["lat"] and point_a["lon"] and point_b["lat"] and point_b["lon"]:
            folium.PolyLine(
                locations=[(point_a["lat"], point_a["lon"]), (point_b["lat"], point_b["lon"])],
                color="blue",
                weight=2.5,
                opacity=0.8
            ).add_to(mymap)

    # Füge Marker nur für Landepunkte hinzu
    for point in flight_data:
        if point["onground"] == 1:  # Nur Landepunkte anzeigen
            folium.Marker(
                location=(point["lat"], point["lon"]),
                popup=f"Zeit: {point['time']}<br>Am Boden: {point['onground']}<br>Hersteller: {aircraft_info['manufacturer']}<br>Flugzeugtyp: {aircraft_info['model']}",
                icon=folium.Icon(color="green", icon="info-sign")
            ).add_to(mymap)

    # Zeige die Karte im Notebook
    display(mymap)
else:
    print(f"Keine Daten für Flugzeug-ID '{selected_icao24}' gefunden.")


Keine Daten für Flugzeug-ID '00cf06' gefunden.


In [16]:
import folium
from IPython.display import display
import random

# Zufällige Farben für die Flugzeuge
def get_random_color():
    return "#{:06x}".format(random.randint(0, 0xFFFFFF))

# Nimm eine beliebige Anzahl zufälliger Flugzeuge aus dem RDD
random_aircrafts = combined_rdd.takeSample(withReplacement=False, num=10)

# Erstelle eine Karte, zentriert auf einen Beispielpunkt
if random_aircrafts:
    # Hole den ersten Punkt zur Zentrierung der Karte
    first_lat = random_aircrafts[0][1]["flight_data"][0]["lat"]
    first_lon = random_aircrafts[0][1]["flight_data"][0]["lon"]
    mymap = folium.Map(location=[first_lat, first_lon], zoom_start=6)

    # Iteriere über die zufälligen Flugzeuge
    for icao24, data in random_aircrafts:
        aircraft_info = data["aircraft_info"]  # Infos über das Flugzeug
        flight_data = data["flight_data"]      # Flugdaten

        # Sichere Abfrage von Typ, Modell und Hersteller mit Standardwerten
        aircraft_type = aircraft_info.get("type", "Unbekannt")
        aircraft_model = aircraft_info.get("model", "Unbekannt")
        aircraft_manufacturer = aircraft_info.get("manufacturer", "Unbekannt")

        # Generiere eine zufällige Farbe für die Linien
        color = get_random_color()

        # Zeichne Linien zwischen aufeinanderfolgenden Punkten
        for i in range(len(flight_data) - 1):
            point_a = flight_data[i]
            point_b = flight_data[i + 1]

            # Zeichne nur Linien, wenn beide Punkte gültige Koordinaten haben
            if point_a["lat"] and point_a["lon"] and point_b["lat"] and point_b["lon"]:
                folium.PolyLine(
                    locations=[(point_a["lat"], point_a["lon"]), (point_b["lat"], point_b["lon"])],
                    color=color,
                    weight=2.5,
                    opacity=0.8
                ).add_to(mymap)

        # Füge Marker nur für Landepunkte hinzu
        for point in flight_data:
            if point["onground"] == 1:  # Nur Landepunkte anzeigen
                folium.Marker(
                    location=(point["lat"], point["lon"]),
                    popup=(
                        f"Flugzeug: {icao24}<br>"
                        f"Hersteller: {aircraft_manufacturer}<br>"
                        f"Modell: {aircraft_model}<br>"
                        f"Zeit: {point['time']}<br>"
                        f"Am Boden: {point['onground']}"
                    ),
                    icon=folium.Icon(color="green", icon="info-sign")
                ).add_to(mymap)

    # Zeige die Karte im Notebook
    display(mymap)
else:
    print("Keine Daten gefunden.")


In [11]:
# Darstellung aller Flugdaten als Heatmap
import folium
from folium.plugins import HeatMap

# Reduziere die Daten durch Sampling (alle 10 Minuten)
# Ein Datensatz
# reduced_data = grouped_rdd.take(1)

reduced_data = combined_rdd.map(lambda x: (
    x[0],  # Flugzeug-ID
    x[1]["flight_data"][::10]  # Wähle jeden 10. Datensatz aus flight_data
))

# Sammle und bereite die Heatmap-Daten vor
heatmap_data = [
    (point["lat"], point["lon"])
    for _, route_data in reduced_data.collect()
    for point in route_data
    if point["lat"] is not None and point["lon"] is not None
]

# Erstelle die Karte
if heatmap_data:
    mymap = folium.Map(location=[heatmap_data[0][0], heatmap_data[0][1]], zoom_start=6)
    HeatMap(heatmap_data, radius=10).add_to(mymap)
    from IPython.display import display
    display(mymap)
else:
    print("Keine gültigen Punkte für die Heatmap gefunden.")
